In [ ]:
import os

import torch

In [ ]:
from PyPDF2 import PdfReader

In [ ]:
reader = PdfReader("/mnt/c/Users/mikol/Desktop/kiid_makro_alokacji_kat._b.pdf")

In [ ]:
page = reader.pages[0]

In [ ]:
page.extract_text()

In [ ]:
with open('linki','r') as file:
    linki = file.read().split('\n')

In [ ]:
import requests
resp = requests.get('https://www.esaliens.pl/~/media/files/pobierz-dokumenty/fs/esa-akcji/2022-09-kah02-esaliens-akcji.ashx')


In [ ]:
resp = requests.get('https://agiofunds.pl')

In [ ]:
from bs4 import BeautifulSoup as bs
soup = bs(resp.content)
soup.find_all('a', recursive=True, href=True)

In [ ]:
resp.headers.get('Content-Type')

In [ ]:
import re
re.findall('dupa', 'smierdzDuPaimidudpakupa', flags=re.I)

In [ ]:
import requests
from bs4 import BeautifulSoup as bs
resp = requests.get('https://esaliens.pl')
soup = bs(resp.content, 'html.parser')
aki = soup.find_all('a', href=True, recursive=True)

In [ ]:
aki[0].get_text()

In [1]:

import requests
import re
from bs4 import BeautifulSoup as bs
import logging
import sys
from urllib.parse import urlparse, urlunparse
from PyPDF2 import PdfReader as pdfr
import io

from requests.exceptions import MissingSchema, InvalidSchema

logging.basicConfig(
    stream=sys.stdout,
    level=logging.INFO,
    format="%(asctime)s-%(levelname)s:%(message)s"
)

logger = logging.getLogger(__name__)


def is_not_bull(a):
    return a.get('href') not in ('/', '#') and not re.findall(r'^tel:', a.get('href')) and not re.findall(r'^mail:', a.get('href')) and not re.findall(r'^mailto:', a.get('href'))

def is_onsite(a, site):
    #logger.debug(f"href netloc is: {urlparse(a.get('href')).netloc} site netloc is: {urlparse(site).netloc}")
    if len(a.get('href')) > 0 and a.get('href')[0] == '/':
        return True
    if site.__contains__(urlparse(a.get('href')).netloc):
        return True
    if a.get('href').__contains__(site):
        return True
    if site == '.'.join(urlparse(a.get('href')).netloc.split('.')[1:]):
        return True
    return False

def add_netloc(a, site):
    link = a.get('href')
    parsed_link = urlparse(link)
    parsed_site = urlparse(site)
    if not parsed_link.netloc:
        a['href'] = urlunparse(
            (
                parsed_site.scheme,
                parsed_site.netloc,
                parsed_link.path,
                parsed_link.params,
                '',
                ''
            )
        )
    return a

def is_not_seen(a, seen):
    if a.get('href') in seen:
        return False
    return True

def is_check(a, site, seen):
    #logger.error(a.get('href'))
    if is_not_bull(a) and is_onsite(a, site) and is_not_seen(a, seen):
        return True
    return False

def is_to_save(a):
    text = a.get_text()
    if re.findall(r'.*KII.*', text, flags=re.I|re.DOTALL) or re.findall(r'.*karta.*', text, flags=re.I|re.DOTALL) or re.findall(r'.*kluczowe.*inwestorów.*', text, flags=re.I|re.DOTALL):
        return True
    return False

def dfs(link):
    """

    :param link: valid url
    :return: list of <a> tags from all pages found on site
    """
    seen = set()
    def dfs_(a):
        if not isinstance(a, str):
            link_ = a.get('href')
        else:
            link_ = a
        seen.add(link_)
        logger.info(f"trying {link_}")
        try:
            resp = requests.get(link_)
            if resp.status_code != 200: # noqa
                logger.warning(f"GET {link_} failed with code: {resp.status_code}")
                return []
            logger.debug(f"GET {link_} content-type: {resp.headers.get('Content-Type')}")
            if resp.headers.get("Content-Type", "").__contains__("text/html"):
                soup = bs(resp.content)
                found_as = soup.find_all("a", href=True, recursive=True)
                to_check_as = [add_netloc(a, link) for a in found_as if is_check(a, link, seen)]
                for a in to_check_as:
                    if is_not_seen(a, seen):
                        dfs_(a)

            elif resp.headers.get("Content-Type", "").__contains__("application/pdf"):
                logger.error(f"found file at: {a.get('href')}")
                if is_to_save(a):
                    if len(pdfr(io.BytesIO(resp.content)).pages) == 2:
                        filename = re.findall(r'(?<=filename=\")(.*)(?=\")',resp.headers.get("Content-Disposition", ""))
                        if len(filename)>0:
                            filename = filename[0]
                        else:
                            filename = a.get('href').split('/')[-1]
                        with open(f'../data/raw/{filename}', 'wb') as file:
                            for chunk in resp.iter_content(chunk_size=1024):
                                file.write(chunk)

            else:
                logger.warn(f"unhandled content-type: {resp.headers.get('Content-Type')}")
        except (MissingSchema, InvalidSchema) as exc:
            logger.warning(f"GET {link_} failed with {exc}")


    dfs_(link)


In [ ]:
import multiprocessing.dummy as mp
pool = mp.Pool(32)
with open('linki', 'r') as file:
    linki = file.read().split('\n')
pool.map(dfs, linki)
pool.close()
pool.join()


2022-10-22 18:40:00,540-INFO:trying https://www.aliortfi.com
2022-10-22 18:40:00,541-INFO:trying https://www.amundi.pl
2022-10-22 18:40:00,541-INFO:trying https://www.baltictfi.pl
2022-10-22 18:40:00,543-INFO:trying https://www.tfi.bnpparibas.pl
2022-10-22 18:40:00,543-INFO:trying https://www.bpstfi.pl
2022-10-22 18:40:00,544-INFO:trying http://www.caspartfi.pl
2022-10-22 18:40:00,546-INFO:trying https://www.eitfi.pl
2022-10-22 18:40:00,546-INFO:trying https://www.esaliens.pl
2022-10-22 18:40:00,547-INFO:trying https://www.generali-investments.pl
2022-10-22 18:40:00,635-INFO:trying https://www.investors.pl
2022-10-22 18:40:00,636-INFO:trying https://www.ipopema.pl
2022-10-22 18:40:00,636-INFO:trying https://www.millenniumtfi.pl
2022-10-22 18:40:00,637-INFO:trying https://www.metlife.pl
2022-10-22 18:40:00,637-INFO:trying https://www.nntfi.pl
2022-10-22 18:40:00,637-INFO:trying https://www.noblefunds.pl
2022-10-22 18:40:00,638-INFO:trying http://www.opera-tfi.pl
2022-10-22 18:40:00,639-

/tmp/ipykernel_17355/907268429.py:112: DeprecationWarning: The 'warn' method is deprecated, use 'warning' instead
  logger.warn(f"unhandled content-type: {resp.headers.get('Content-Type')}")


2022-10-22 18:40:37,427-INFO:trying https://www.pKotfi.pl/media_files/810b6758-9870-4a6e-88c2-7175cbf2a105.pdf
2022-10-22 18:40:37,520-ERROR:found file at: https://www.pKotfi.pl/media_files/810b6758-9870-4a6e-88c2-7175cbf2a105.pdf
2022-10-22 18:40:37,545-INFO:trying https://www.rockbridge.pl/sprawozdania-funduszy
2022-10-22 18:40:37,568-INFO:trying https://www.pKotfi.pl/media_files/1e5a01cc-9a64-4511-9169-4d7739471ee8.pdf
2022-10-22 18:40:37,611-INFO:trying https://www.noblefunds.pl/dokumenty-procedury
2022-10-22 18:40:37,680-ERROR:found file at: https://www.pKotfi.pl/media_files/1e5a01cc-9a64-4511-9169-4d7739471ee8.pdf
2022-10-22 18:40:37,722-INFO:trying https://www.pKotfi.pl/media_files/d1ec9dba-6a7a-48eb-b360-f779d2b8f903.pdf
2022-10-22 18:40:37,797-INFO:trying https://www.eitfi.pl/download/34ad9bc83e3c72c62281cb2c744ac966
2022-10-22 18:40:37,829-ERROR:found file at: https://www.pKotfi.pl/media_files/d1ec9dba-6a7a-48eb-b360-f779d2b8f903.pdf
2022-10-22 18:40:37,833-INFO:trying https:

/home/mikolaj/.dataspell/lib/python3.10/site-packages/bs4/builder/__init__.py:545: XMLParsedAsHTMLWarning: It looks like you're parsing an XML document using an HTML parser. If this really is an HTML document (maybe it's XHTML?), you can ignore or filter this warning. If it's XML, you should know that using an XML parser will be more reliable. To parse this document as XML, make sure you have the lxml package installed, and pass the keyword argument `features="xml"` into the BeautifulSoup constructor.
  warnings.warn(


2022-10-22 18:42:33,747-INFO:trying https://www.eitfi.pl/download/33853141e0873909be88f5c3e6144cc6
2022-10-22 18:42:33,758-INFO:trying https://www.rockbridge.pl/notowania/historia/76
2022-10-22 18:42:33,793-WARNING:GET https://www.vigcq-tfi.pl/language/ failed with code: 404
2022-10-22 18:42:33,803-INFO:trying https://www.addtoany.com/add_to/twitter?linkurl=https://www.vigcq-tfi.pl/aktualnosci,vig-c-quadrat-z-licencja-knf/cid/4.html&linkname=VIG+%2F+C-QUADRAT+z+licencj%C4%85+KNF
2022-10-22 18:42:33,810-ERROR:found file at: https://www.noblefunds.pl/images/SFIO/prospekty/2020_06_24_Prospekt_Noble_Funds_SFIO.pdf
2022-10-22 18:42:33,818-INFO:trying https://www.noblefunds.pl/images/SFIO/prospekty/2020_06_24_Ogloszenie_o_zmianach_prospektu_SFIO.pdf
2022-10-22 18:42:33,873-WARNING:unhandled content-type: text/csv; charset=UTF-8
2022-10-22 18:42:33,875-INFO:trying https://www.rockbridge.pl/fundusze/rockbridge-fiz-bezpieczna-inwestycja-2
2022-10-22 18:42:33,886-ERROR:found file at: https://www

In [ ]:
resp = requests.get('https://www.amundi.pl/Inwestorzy_indywidualni/Pobierz-materialy/Amundi-Parasolowy-FIO')
soup = bs(resp.content)
soup.find_all()

In [ ]:
soup.find_all('a', href=True, recursive=True, text=re.compile('.*kiid.*', flags=re.I|re.DOTALL))

In [ ]:
bs(''' <a class="card document" data-event="C" data-event-label="amundiparasolowyfio-pobierzdokumenty::kiid-amundi-subfundusz-ostrozny-inwestor-kat-a-2022-05-31-pdf" data-event-type="T" data-event-zone="click" href="https://www.amundi.pl/Inwestorzy_indywidualni/ezjscore/call/ezjscamundibuzz::sfForwardFront::paramsList=service=ProxyGedApi&amp;routeId=_dl_7bf344cf-486a-48c2-8dac-700607952b4c_download">
 <h6>KIID Amundi Ostrożny Inwestor kat. A</h6>
 <span class="nota">Publikacja: 05-2022</span>
 </a>''', 'html.parser').find_all('a', href=True, recursive=True)

In [ ]:
urlparse("https://www.amundi.pl/Inwestorzy_indywidualni/ezjscore/call/ezjscamundibuzz::sfForwardFront::paramsList=service=ProxyGedApi&amp;routeId=_dl_7bf344cf-486a-48c2-8dac-700607952b4c_download")